# Running hyperparameter optimization on Chemprop model using RayTune

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/chemprop/chemprop/blob/main/examples/hpopting.ipynb)

In [1]:
# Install chemprop from GitHub if running in Google Colab
import os

if os.getenv("COLAB_RELEASE_TAG"):
    try:
        import chemprop
    except ImportError:
        !git clone https://github.com/chemprop/chemprop.git
        %cd chemprop
        !pip install ".[hpopt]"
        %cd examples

## Import packages

In [2]:
from pathlib import Path
import sys

import pandas as pd
from lightning import pytorch as pl
import numpy as np
import ray
from ray import tune
from ray.train import CheckpointConfig, RunConfig, ScalingConfig
from ray.train.lightning import (RayDDPStrategy, RayLightningEnvironment,
                                 RayTrainReportCallback, prepare_trainer)
from ray.train.torch import TorchTrainer
from ray.tune.search.hyperopt import HyperOptSearch
from ray.tune.search.optuna import OptunaSearch
from ray.tune.schedulers import FIFOScheduler
import torch

from chemprop import data, featurizers, models, nn

# sys.path.insert(0, '../agenticadmet')
# from raytune_extra import RayTrainReportCallback

In [3]:
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)
torch.cuda.manual_seed_all(RANDOM_SEED)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

In [4]:
input_path = Path('../data/asap/datasets/rnd_splits/split_0.csv')
num_workers = 0 # number of workers for dataloader. 0 means using main process for data loading
smiles_column = 'smiles_std' # name of the column containing SMILES strings
target_columns = ['LogHLM', 'LogMLM', 'LogD', 'LogKSOL', 'LogMDR1-MDCKII'] # list of names of the columns containing targets

hpopt_save_dir = Path('../output/asap/rnd_splits/chemprop/run_0/split_0/hpopt') # directory to save hyperopt results
hpopt_save_dir.mkdir(exist_ok=True)

## Load data

In [5]:
df_input = pd.read_csv(input_path)
df_input

smiles    HLM   KSOL  LogD  \
0    COC1=CC=CC(Cl)=C1NC(=O)N1CCC[C@H](C(N)=O)C1 |a...    NaN    NaN   0.3   
1    O=C(NCC(F)F)[C@H](NC1=CC2=C(C=C1Br)CNC2)C1=CC(...    NaN  333.0   2.9   
2    O=C(NCC(F)F)[C@H](NC1=CC=C2CNCC2=C1)C1=CC(Br)=...    NaN    NaN   0.4   
3    NC(=O)[C@H]1CCCN(C(=O)CC2=CC=CC3=C2C=CO3)C1 |&...    NaN  376.0   1.0   
4     CC1=CC(CC(=O)N2CCC[C@H](C(N)=O)C2)=CC=N1 |&1:11|    NaN  375.0  -0.3   
..                                                 ...    ...    ...   ...   
429        CC(C)NC[C@H](O)COC1=CC=CC2=CC=CC=C12 |&1:5|   25.5    NaN   NaN   
430               O=C(O)CC1=CC=CC=C1NC1=C(Cl)C=CC=C1Cl  216.0    NaN   NaN   
431          NCC1=CC(Cl)=CC(C(=O)NC2=CC=C3CNCC3=C2)=C1    NaN    NaN   2.0   
432        COC(=O)NC1=NC2=CC=C(C(=O)C3=CC=CC=C3)C=C2N1    NaN    NaN   2.9   
433  CC1=NC=CN1C[C@H]1CCC2=C(C1=O)C1=CC=CC=C1N2C |&...    NaN  127.0   NaN   

       MLM  MDR1-MDCKII                                         smiles_std  \
0      NaN          2.0           COc1cccc(Cl)c1NC(=O)N1CCC[C@H](C(N)=O)C1   
1      NaN          0.2  O=C(NCC(F)F)[C@H](Nc1cc2c(cc1Br)CNC2)c1cc(Cl)c...   
2      NaN          0.5  O=C(NCC(F)F)[C@H](Nc1ccc2c(c1)CNC2)c1cc(Br)cc2...   
3      NaN          8.5            NC(=O)[C@H]1CCCN(C(=O)Cc2cccc3occc23)C1   
4      NaN          0.9              Cc1cc(CC(=O)N2CCC[C@H](C(N)=O)C2)ccn1   
..     ...          ...                                                ...   
429   63.0          NaN                    CC(C)NC[C@H](O)COc1cccc2ccccc12   
430  386.0          NaN                     O=C(O)Cc1ccccc1Nc1c(Cl)cccc1Cl   
431    NaN          NaN              NCc1cc(Cl)cc(C(=O)Nc2ccc3c(c2)CNC3)c1   
432    NaN          NaN            COC(=O)Nc1nc2ccc(C(=O)c3ccccc3)cc2[nH]1   
433    NaN          NaN              Cc1nccn1C[C@H]1CCc2c(c3ccccc3n2C)C1=O   

                                          cxsmiles_std  mol_idx smiles_ext  \
0      COc1cccc(Cl)c1NC(=O)N1CCC[C@H](C(N)=O)C1 |a:16|      191     |a:16|   
1    O=C(NCC(F)F)[C@H](Nc1cc2c(cc1Br)CNC2)c1cc(Cl)c...      335     |&1:7|   
2    O=C(NCC(F)F)[C@H](Nc1ccc2c(c1)CNC2)c1cc(Br)cc2...      336     |&1:7|   
3       NC(=O)[C@H]1CCCN(C(=O)Cc2cccc3occc23)C1 |&1:3|      300     |&1:3|   
4        Cc1cc(CC(=O)N2CCC[C@H](C(N)=O)C2)ccn1 |&1:11|      249    |&1:11|   
..                                                 ...      ...        ...   
429             CC(C)NC[C@H](O)COc1cccc2ccccc12 |&1:5|       22     |&1:5|   
430                     O=C(O)Cc1ccccc1Nc1c(Cl)cccc1Cl      380        NaN   
431              NCc1cc(Cl)cc(C(=O)Nc2ccc3c(c2)CNC3)c1      303        NaN   
432            COC(=O)Nc1nc2ccc(C(=O)c3ccccc3)cc2[nH]1      166        NaN   
433       Cc1nccn1C[C@H]1CCc2c(c3ccccc3n2C)C1=O |&1:7|      268     |&1:7|   

       LogHLM    LogMLM   LogKSOL  LogMDR1-MDCKII  split  
0         NaN       NaN       NaN        0.477121    val  
1         NaN       NaN  2.523746        0.079181  train  
2         NaN       NaN       NaN        0.176091  train  
3         NaN       NaN  2.576341        0.977724  train  
4         NaN       NaN  2.575188        0.278754  train  
..        ...       ...       ...             ...    ...  
429  1.423246  1.806180       NaN             NaN    val  
430  2.336460  2.587711       NaN             NaN    val  
431       NaN       NaN       NaN             NaN  train  
432       NaN       NaN       NaN             NaN  train  
433       NaN       NaN  2.107210             NaN  train  

[434 rows x 15 columns]

## Make data points, splits, and datasets

In [6]:
train_data, val_data = [], []
for _, row in df_input.iterrows():
    dp = data.MoleculeDatapoint.from_smi(row[smiles_column], row[target_columns].values)
    if row['split'] == 'train':
        train_data.append(dp)
    elif row['split'] == 'val':
        val_data.append(dp)

In [7]:
featurizer = featurizers.SimpleMoleculeMolGraphFeaturizer()

train_dset = data.MoleculeDataset(train_data, featurizer)
# scaler = train_dset.normalize_targets()

val_dset = data.MoleculeDataset(val_data, featurizer)
# val_dset.normalize_targets(scaler)

# Define helper function to train the model

In [8]:
# def train_model(config, train_dset, val_dset, num_workers, scaler):
def train_model(config, train_dset, val_dset, num_workers):
    # config is a dictionary containing hyperparameters used for the trial
    depth = int(config["depth"])
    ffn_hidden_dim = int(config["ffn_hidden_dim"])
    ffn_num_layers = int(config["ffn_num_layers"])
    message_hidden_dim = int(config["message_hidden_dim"])
    dropout = 0.2

    train_loader = data.build_dataloader(train_dset, num_workers=num_workers, shuffle=True)
    val_loader = data.build_dataloader(val_dset, num_workers=num_workers, shuffle=False)

    mp = nn.BondMessagePassing(d_h=message_hidden_dim, depth=depth, dropout=dropout)
    agg = nn.MeanAggregation()
    # output_transform = nn.UnscaleTransform.from_standard_scaler(scaler)
    # ffn = nn.RegressionFFN(output_transform=output_transform, input_dim=message_hidden_dim, hidden_dim=ffn_hidden_dim, n_layers=ffn_num_layers)
    ffn = nn.RegressionFFN(
        n_tasks=len(target_columns),
        output_transform=None, input_dim=message_hidden_dim, hidden_dim=ffn_hidden_dim, n_layers=ffn_num_layers,
        dropout=dropout
    )
    batch_norm = True
    metric_list = [nn.metrics.MAE(), nn.metrics.R2Score()]
    model = models.MPNN(mp, agg, ffn, batch_norm, metric_list)

    trainer = pl.Trainer(
        accelerator="auto",
        devices=1,
        max_epochs=200, # number of epochs to train for
        # below are needed for Ray and Lightning integration
        strategy=RayDDPStrategy(),
        callbacks=[RayTrainReportCallback()],
        plugins=[RayLightningEnvironment()],
        enable_progress_bar=False,
        enable_checkpointing=False
    )

    trainer = prepare_trainer(trainer)
    trainer.fit(model, train_loader, val_loader)

## Define parameter search space

In [9]:
search_space = {
    "depth": tune.qrandint(lower=2, upper=6, q=1),
    "ffn_hidden_dim": tune.qrandint(lower=300, upper=2400, q=100),
    "ffn_num_layers": tune.qrandint(lower=1, upper=3, q=1),
    "message_hidden_dim": tune.qrandint(lower=300, upper=2400, q=100),
}

In [ ]:
ray.shutdown()
ray.init(include_dashboard=False)

scheduler = FIFOScheduler()

# Scaling config controls the resources used by Ray
scaling_config = ScalingConfig(
    num_workers=1,
    use_gpu=True, # set to True if you want to use GPU
)

# Checkpoint config controls the checkpointing behavior of Ray
checkpoint_config = CheckpointConfig(
    num_to_keep=1, # number of checkpoints to keep
    checkpoint_score_attribute="val_loss", # Save the checkpoint based on this metric
    checkpoint_score_order="min", # Save the checkpoint with the lowest metric value
    checkpoint_frequency=0,        # Do not checkpoint during training
)

run_config = RunConfig(
    checkpoint_config=checkpoint_config,
    storage_path=(hpopt_save_dir / "ray_results").absolute(), # directory to save the results
)

ray_trainer = TorchTrainer(
    lambda config: train_model(
        # config, train_dset, val_dset, num_workers, scaler
        config, train_dset, val_dset, num_workers
    ),
    scaling_config=scaling_config,
    run_config=run_config,
)

search_alg = HyperOptSearch(
    n_initial_points=10, # number of random evaluations before tree parzen estimators
    random_state_seed=RANDOM_SEED,
)

# OptunaSearch is another search algorithm that can be used
# search_alg = OptunaSearch()

tune_config = tune.TuneConfig(
    metric="val_loss",
    mode="min",
    num_samples=30, # number of trials to run
    scheduler=scheduler,
    search_alg=search_alg,
    trial_dirname_creator=lambda trial: str(trial.trial_id), # shorten filepaths

)

tuner = tune.Tuner(
    ray_trainer,
    param_space={
        "train_loop_config": search_space,
    },
    tune_config=tune_config,
)

# Start the hyperparameter search
results = tuner.fit()

(RayTrainWorker pid=884210) Setting up process group for: env:// [rank=0, world_size=1]
(TorchTrainer pid=884032) Started distributed worker processes: 
(TorchTrainer pid=884032) - (node_id=e144ce729767a603c60c078cf396230afd874a47aae8ebb95818699e, ip=10.128.0.3, pid=884210) world_rank=0, local_rank=0, node_rank=0
(RayTrainWorker pid=884210) GPU available: True (cuda), used: True
(RayTrainWorker pid=884210) TPU available: False, using: 0 TPU cores
(RayTrainWorker pid=884210) HPU available: False, using: 0 HPUs
(RayTrainWorker pid=884210) LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
(RayTrainWorker pid=884210) Loading `train_dataloader` to estimate number of stepping batches.
(RayTrainWorker pid=884210) /opt/conda/envs/admet/lib/python3.11/site-packages/lightning/pytorch/trainer/connectors/data_connector.py:425: The 'train_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=15` in the `DataLoader` to 

(RayTrainWorker pid=926691) [rank0]:[W302 04:59:48.190631592 ProcessGroupNCCL.cpp:1496] Warning: WARNING: destroy_process_group() was not called before program exit, which can leak resources. For more info, please see https://pytorch.org/docs/stable/distributed.html#shutdown (function operator())


## Hyperparameter optimization results

In [24]:
# results of all trials
result_df = results.get_dataframe()
results_df = result_df.sort_values('val/mae')
results_df

train_loss  train_loss_step   val/mae    val/r2  val_loss  \
23    0.063088         0.049382  0.320957  0.772473  0.216594   
18    0.054118         0.042587  0.321334  0.776484  0.212775   
16    0.053271         0.059022  0.326163  0.763556  0.225082   
25    0.054896         0.051933  0.326662  0.773306  0.215800   
13    0.047769         0.044336  0.326847  0.767792  0.221050   
29    0.075725         0.084574  0.327974  0.741446  0.246129   
10    0.053740         0.061331  0.327978  0.755122  0.233111   
19    0.048885         0.035608  0.328147  0.753925  0.234250   
24    0.047129         0.039629  0.328355  0.762753  0.225846   
14    0.057202         0.046290  0.329010  0.732047  0.255076   
2     0.068232         0.057665  0.329687  0.749092  0.238850   
1     0.048132         0.041259  0.330025  0.740848  0.246699   
28    0.049775         0.046454  0.330270  0.768457  0.220416   
27    0.049771         0.052301  0.331778  0.759454  0.228987   
6     0.059006         0.072001  0.335024  0.735992  0.251321   
8     0.047513         0.042465  0.335115  0.761512  0.227028   
20    0.058198         0.040192  0.335281  0.746030  0.241765   
21    0.051705         0.049994  0.336435  0.738716  0.248728   
3     0.054152         0.049349  0.336702  0.742979  0.244670   
15    0.066256         0.059197  0.337160  0.759644  0.228806   
22    0.053218         0.047669  0.337232  0.741491  0.246086   
26    0.063988         0.052492  0.342334  0.742635  0.244997   
5     0.050462         0.034162  0.346877  0.731047  0.256029   
11    0.051870         0.044582  0.351413  0.730966  0.256106   
17    0.048317         0.048017  0.352136  0.741222  0.246343   
0     0.050816         0.035582  0.354785  0.741035  0.246521   
12    0.049533         0.040564  0.361335  0.734235  0.252993   
9     0.050226         0.042951  0.369408  0.705839  0.280025   
7     0.050765         0.043843  0.385529  0.692541  0.292685   
4     0.046184         0.040345  0.386104  0.695363  0.289997   

    train_loss_epoch  epoch  step   timestamp checkpoint_dir_name  ...  \
23          0.063088    199  1200  1740890722   checkpoint_000199  ...   
18          0.054118    199  1200  1740889819   checkpoint_000199  ...   
16          0.053271    199  1200  1740889515   checkpoint_000199  ...   
25          0.054896    199  1200  1740891023   checkpoint_000199  ...   
13          0.047769    199  1200  1740888810   checkpoint_000199  ...   
29          0.075725    199  1200  1740891586   checkpoint_000199  ...   
10          0.053740    199  1200  1740888311   checkpoint_000199  ...   
19          0.048885    199  1200  1740890031   checkpoint_000199  ...   
24          0.047129    199  1200  1740890891   checkpoint_000199  ...   
14          0.057202    199  1200  1740889249   checkpoint_000199  ...   
2           0.068232    199  1200  1740886564   checkpoint_000199  ...   
1           0.048132    199  1200  1740886472   checkpoint_000199  ...   
28          0.049775    199  1200  1740891462   checkpoint_000199  ...   
27          0.049771    199  1200  1740891300   checkpoint_000199  ...   
6           0.059006    199  1200  1740887550   checkpoint_000199  ...   
8           0.047513    199  1200  1740887992   checkpoint_000199  ...   
20          0.058198    199  1200  1740890154   checkpoint_000199  ...   
21          0.051705    199  1200  1740890350   checkpoint_000199  ...   
3           0.054152    199  1200  1740886850   checkpoint_000199  ...   
15          0.066256    199  1200  1740889364   checkpoint_000199  ...   
22          0.053218    199  1200  1740890596   checkpoint_000199  ...   
26          0.063988    199  1200  1740891121   checkpoint_000199  ...   
5           0.050462    199  1200  1740887328   checkpoint_000199  ...   
11          0.051870    199  1200  1740888467   checkpoint_000199  ...   
17          0.048317    199  1200  1740889676   checkpoint_000199  ...   
0           0.050816    199  1200  1740886138   checkpoint_00019

In [23]:
results_df.to_csv(hpopt_save_dir / 'results.csv', index=False)

In [ ]:
ray.shutdown()